In [1]:
import pandas as pd
import numpy as np
import sqlite3
import matplotlib.pyplot as plt
import os

from sklearn.ensemble import ExtraTreesClassifier
from sklearn.ensemble import RandomForestClassifier
from sklearn.linear_model import LogisticRegression
from sklearn.discriminant_analysis import LinearDiscriminantAnalysis
from sklearn.discriminant_analysis import QuadraticDiscriminantAnalysis
from sklearn.naive_bayes import GaussianNB
from sklearn.ensemble import VotingClassifier

from sklearn.model_selection import train_test_split
from sklearn.metrics import accuracy_score
from sklearn.base import clone

In [2]:
#connect to the S&P 500 database file and create an associated cursor
conn = sqlite3.connect("SP500_stats_5y.db")
c = conn.cursor()

In [3]:
c.execute("SELECT * FROM CompanyInfo")
companies_df = pd.DataFrame(c.fetchall(), columns = [x[0] for x in c.description])

AllSymbols = list(companies_df['Symbol'])
AllSectors = list(companies_df['Sector'])
AllIndustries = list(companies_df['Industry'])

print("Companies excluded from analysis:")
#Let's skip the stocks without a full data set for simplicity
Skips = []
for i in range(len(AllSymbols)):
    Symbol = AllSymbols[i]
    
    c.execute("SELECT * FROM "+Symbol.replace('.','_')+"_stats")
    test_df = pd.DataFrame(c.fetchall(), columns = [x[0] for x in c.description])
    
    if (not len(test_df)==1281) or Symbol=='GSPC':
        print(Symbol, len(test_df),list(test_df['Date'])[0],list(test_df['Date'])[-1])
        Skips.append(i)

for i in reversed(Skips):
    AllSymbols.remove(AllSymbols[i])
    AllSectors.remove(AllSectors[i])
    AllIndustries.remove(AllIndustries[i])

Companies excluded from analysis:
CARR 484 2020-03-19 2022-02-16
CDAY 961 2018-04-26 2022-02-16
CEG 21 2022-01-19 2022-02-16
CTVA 690 2019-05-24 2022-02-16
DOW 736 2019-03-20 2022-02-16
FOXA 742 2019-03-12 2022-02-16
FOX 741 2019-03-13 2022-02-16
IR 1201 2017-05-12 2022-02-16
MRNA 805 2018-12-07 2022-02-16
OGN 193 2021-05-14 2022-02-16
OTIS 484 2020-03-19 2022-02-16
GSPC 1281 2017-01-18 2022-02-16


In [4]:
ints_12mo = [[0,365],[366,730],[731,1095],[1096,1460]]

#Import data from PairsIdentification notebook to use as the basis for the training/validation data
find_pairs_df = pd.read_csv('finding_pairs_stats.csv')
find_pairs_df = find_pairs_df.sort_values(by='MeanPairsRatio',ascending=False).reset_index(drop=True)
find_pairs_df = find_pairs_df.drop(['Unnamed: 0','TotSigma','6moAvg','12moAvg'],1)

find_pairs_df


Symbol1           S1Sector             S1Industry Symbol2  \
0          AAL        Industrials               Airlines     APA   
1          UAA  Consumer Cyclical  Apparel Manufacturing     VTR   
2          PXD             Energy          Oil & Gas E&P    WYNN   
3          AAL        Industrials               Airlines    FANG   
4          HES             Energy          Oil & Gas E&P    ULTA   
...        ...                ...                    ...     ...   
122755     AAL        Industrials               Airlines    ENPH   
122756    ENPH         Technology                  Solar    REGN   
122757     EOG             Energy          Oil & Gas E&P    PENN   
122758    CTXS         Technology   Software—Application    ENPH   
122759    ENPH         Technology                  Solar      KR   

                  S2Sector                  S2Industry  PairTrade1  \
0                   Energy               Oil & Gas E&P  153.156120   
1              Real Estate  REIT—Healthcare Facilities  128.047603   
2        Consumer Cyclical           Resorts & Casinos  119.593367   
3                   Energy               Oil & Gas E&P   87.636641   
4        Consumer Cyclical            Specialty Retail  120.579899   
...                    ...                         ...         ...   
122755          Technology                       Solar  -50.803680   
122756          Healthcare               Biotechnology  -24.123321   
122757   Consumer Cyclical           Resorts & Casinos  137.561992   
122758          Technology                       Solar  -21.820131   
122759  Consumer Defensive              Grocery Stores  -30.435064   

        SP500Trade1  PairTrade2  SP500Trade2  PairTrade3  SP500Trade3  \
0         94.600368  155.414642    125.04929  240.999797   114.082979   
1         94.600368  139.914720    125.04929  266.889216   114.082979   
2         94.600368  136.382649    125.04929  275.753610   114.082979   
3         94.600368  128.540957    125.04929  302.104377   114.082979   
4         94.600368  125.783828    125.04929  269.205452   114.082979   
...             ...         ...          ...         ...          ...   
122755    94.600368  -90.762267    125.04929 -198.343338   114.082979   
122756    94.600368  -86.590170    125.04929 -234.502064   114.082979   
122757    94.600368  110.584790    125.04929 -599.718360   114.082979   
122758    94.600368  -79.649702    125.04929 -260.580727   114.082979   
122759    94.600368  -85.439827    125.04929 -280.709603   114.082979   

        MeanPairsRatio   LastAvgDiff  LastSymbol1Mean  LastSymbol2Mean  
0           164.673903  2.830848e-17        30.365462        26.391106  
1           160.263481 -4.246271e-17        21.550598        57.579155  
2           159.328027 -9.200255e-17       130.673107       121.001743  
3           155.298559  5.705927e-17        30.365462        91.046464  
4           154.485694 -7.077119e-17        59.550600       299.323109  
...                ...           ...              ...              ...  
122755     -101.850777 -5.661695e-17        30.365462        18.798287  
122756     -103.440754  8.492543e-17        18.798287       342.344104  
122757     -105.345279  1.344653e-16        76.879122        21.336175  
122758     -108.485212 -2.830848e-17        99.295795        18.798287  
122759     -118.832997 -2.830848e-17        18.798287        23.954691  

[122760 rows x 16 columns]

In [5]:
#Import S&P 500 data outside of the function, since we will need it for every call
c.execute("SELECT * FROM GSPC_stats")
SP500_df = pd.DataFrame(c.fetchall(), columns = [x[0] for x in c.description])

In [6]:
def GetPriorYearStats(Symbol,train_dates):
    c.execute("SELECT * FROM "+Symbol.replace('.','_')+"_stats")
    stats_df = pd.DataFrame(c.fetchall(), columns = [x[0] for x in c.description])

    monthly_returns = []
    monthly_market_ratios = []
    tracking_date = train_dates[0]
    for ctr_ind in range(12):
        month_range_df = stats_df[(stats_df['date_int'] >= tracking_date ) & (stats_df['date_int'] <= tracking_date+30 ) ]
        month_SP500_df = SP500_df[(SP500_df['date_int'] >= tracking_date ) & (SP500_df['date_int'] <= tracking_date+30 ) ]

        start_val = float(month_range_df[month_range_df.index==min(month_range_df.index)]['Open'])
        end_val = float(month_range_df[month_range_df.index==max(month_range_df.index)]['Close'])
        monthly_return = end_val / start_val

        start_sp500 = float(month_SP500_df[month_SP500_df.index==min(month_SP500_df.index)]['Open'])
        end_sp500 = float(month_SP500_df[month_SP500_df.index==max(month_SP500_df.index)]['Close'])
        monthly_sp500 = start_sp500/end_sp500

        monthly_returns.append(monthly_return)
        monthly_market_ratios.append(monthly_return/monthly_sp500)

        #print(tracking_date,tracking_date+30,monthly_return,monthly_return/monthly_sp500)
        tracking_date += 30
    
    year_range_df = stats_df[(stats_df['date_int'] >= train_dates[0] ) & (stats_df['date_int'] <= train_dates[1] ) ]
    start_val = float(year_range_df[year_range_df.index==min(year_range_df.index)]['Open'])
    end_val = float(year_range_df[year_range_df.index==max(year_range_df.index)]['Close'])
    yearly_return = end_val / start_val
    
    year_SP500_df = SP500_df[(SP500_df['date_int'] >= train_dates[0] ) & (SP500_df['date_int'] <= train_dates[1] ) ]
    start_sp500 = float(year_SP500_df[year_SP500_df.index==min(year_SP500_df.index)]['Open'])
    end_sp500 = float(year_SP500_df[year_SP500_df.index==max(year_SP500_df.index)]['Close'])
    yearly_sp500 = start_sp500/end_sp500
    
    return monthly_returns, monthly_market_ratios, yearly_return, yearly_return/yearly_sp500


In [7]:
if os.path.isfile('sym_stats_data.csv'):
    print('Dataframe already computed. Importing now.')
    sym_stats_df = pd.read_csv('sym_stats_data.csv').drop('Unnamed: 0',1)
else:
    sym_stats_df = pd.DataFrame(columns = ['Trading Year','Symbol','Sector','Industry',
                                           'M1_return','M2_return','M3_return','M4_return', 'M5_return', 'M6_return',
                                           'M7_return','M8_return','M9_return','M10_return','M11_return','M12_return',
                                           'M1_ratio', 'M2_ratio', 'M3_ratio', 'M4_ratio',  'M5_ratio',  'M6_ratio',
                                           'M7_ratio', 'M8_ratio', 'M9_ratio', 'M10_ratio', 'M11_ratio', 'M12_ratio',
                                           'Return','Ratio',
                                           ])

    print('% Complete:')
    ctr = 0
    for i in range(len(AllSymbols)):
        ctr += 1
        print(100.0*ctr/len(AllSymbols))
        for year_int in [1,2,3,4]:
            M_returns,M_ratios,S_return,S_ratio = GetPriorYearStats(AllSymbols[i],ints_12mo[year_int-1])

            sym_stats_df = sym_stats_df.append({'Trading Year':year_int,'Symbol':AllSymbols[i],'Sector':AllSectors[i],'Industry':AllIndustries[i],
                                                'M1_return':M_returns[0],'M2_return':M_returns[1],'M3_return':M_returns[2],'M4_return':M_returns[3],
                                                'M5_return':M_returns[4],'M6_return':M_returns[5],'M7_return':M_returns[6],'M8_return':M_returns[7],
                                                'M9_return':M_returns[8],'M10_return':M_returns[9],'M11_return':M_returns[10],'M12_return':M_returns[11],
                                                'M1_ratio':M_ratios[0],'M2_ratio':M_ratios[1],'M3_ratio':M_ratios[2],'M4_ratio':M_ratios[3],
                                                'M5_ratio':M_ratios[4],'M6_ratio':M_ratios[5],'M7_ratio':M_ratios[6],'M8_ratio':M_ratios[7],
                                                'M9_ratio':M_ratios[8],'M10_ratio':M_ratios[9],'M11_ratio':M_ratios[10],'M12_ratio':M_ratios[11],
                                                'Return':S_return,'Ratio':S_ratio
                                                }, ignore_index = True)

Dataframe already computed. Importing now.


In [8]:
sym_stats_df

Trading Year Symbol                  Sector  \
0                1    MMM             Industrials   
1                2    MMM             Industrials   
2                3    MMM             Industrials   
3                4    MMM             Industrials   
4                1    AOS             Industrials   
...            ...    ...                     ...   
1975             4   MDLZ  Communication Services   
1976             1   VIAC                     NaN   
1977             2   VIAC                     NaN   
1978             3   VIAC                     NaN   
1979             4   VIAC                     NaN   

                            Industry  M1_return  M2_return  M3_return  \
0                      Conglomerates   1.035084   1.048683   0.988053   
1                      Conglomerates   0.965274   0.991089   0.942831   
2                      Conglomerates   1.082813   1.001876   1.047273   
3                      Conglomerates   0.881599   0.857508   1.063539   
4                    Medical Devices   1.038043   1.055218   0.961193   
...                              ...        ...        ...        ...   
1975  Specialty Industrial Machinery   1.085517   0.771201   1.146881   
1976                             NaN   1.051040   1.027786   1.020442   
1977                             NaN   0.923321   0.910342   1.000786   
1978                             NaN   1.031364   0.912253   1.114681   
1979                             NaN   0.888608   0.365805   1.300412   

      M4_return  M5_return  M6_return  ...  M5_ratio  M6_ratio  M7_ratio  \
0      1.035024   1.096349   0.989159  ...  1.132880  0.995877  0.983261   
1      0.918734   1.018304   0.998371  ...  1.032584  1.016358  1.026578   
2      0.778141   1.031975   1.031040  ...  1.059503  1.062396  0.906108   
3      1.031226   1.123213   0.997691  ...  1.200165  1.025877  1.080178   
4      1.059407   1.066943   1.006640  ...  1.102494  1.013477  0.960878   
...         ...        ...        ...  ...       ...       ...       ...   
1975   0.960249   1.038825   1.036985  ...  1.109996  1.066281  1.098768   
1976   0.901329   1.028085   1.039087  ...  1.062342  1.046144  1.043992   
1977   1.009559   1.075439   1.039643  ...  1.090521  1.058374  0.929923   
1978   0.924517   1.019897   1.039279  ...  1.047103  1.070886  0.816021   
1979   1.260754   1.282107   1.050897  ...  1.369945  1.080586  1.128277   

      M8_ratio  M9_ratio  M10_ratio  M11_ratio  M12_ratio    Return     Ratio  
0     1.048810  1.047727   1.063027   1.079049   1.063200  1.414757  1.744507  
1     1.053662  0.943732   1.008586   0.963841   0.978177  0.815212  0.776848  
2     1.066458  0.945133   1.099931   1.011221   1.107136  0.965196  1.209135  
3     1.023778  1.017434   1.061435   1.024634   0.981205  0.944263  1.071421  
4     1.082328  1.077292   0.969939   1.050683   1.118436  1.390181  1.714204  
...        ...       ...        ...        ...        ...       ...       ...  
1975  1.043748  1.029455   1.042724   0.995595   1.042232  1.064940  1.208348  
1976  0.882205  1.007312   0.998847   1.069467   1.060109  0.960000  1.183756  
1977  1.079133  0.952946   1.035096   0.818870   0.997066  0.820803  0.782177  
1978  1.026270  0.873697   1.055511   1.038948   1.064518  0.807609  1.011720  
1979  1.111337  0.945728   1.141218   1.149308   1.246830  1.193880  1.354652  

[1980 rows x 30 columns]

In [9]:
if os.path.isfile('train_set_data.csv'):
    print('Dataframe already computed. Importing now.')
    train_set_df = pd.read_csv('train_set_data.csv').drop('Unnamed: 0',1)
else:
    train_set_df = pd.DataFrame(columns = ['Symbol1','S1Sector','S1Industry','Symbol2','S2Sector','S2Industry',
                                           'M1S1_return','M2S1_return','M3S1_return','M4S1_return', 'M5S1_return', 'M6S1_return',
                                           'M7S1_return','M8S1_return','M9S1_return','M10S1_return','M11S1_return','M12S1_return',
                                           'M1S1_ratio', 'M2S1_ratio', 'M3S1_ratio', 'M4S1_ratio',  'M5S1_ratio',  'M6S1_ratio',
                                           'M7S1_ratio', 'M8S1_ratio', 'M9S1_ratio', 'M10S1_ratio', 'M11S1_ratio', 'M12S1_ratio',
                                           'M1S2_return','M2S2_return','M3S2_return','M4S2_return', 'M5S2_return', 'M6S2_return',
                                           'M7S2_return','M8S2_return','M9S2_return','M10S2_return','M11S2_return','M12S2_return',
                                           'M1S2_ratio', 'M2S2_ratio', 'M3S2_ratio', 'M4S2_ratio',  'M5S2_ratio',  'M6S2_ratio',
                                           'M7S2_ratio', 'M8S2_ratio', 'M9S2_ratio', 'M10S2_ratio', 'M11S2_ratio', 'M12S2_ratio',
                                           'M1S1S2_ratio','M2S1S2_ratio','M3S1S2_ratio','M4S1S2_ratio','M5S1S2_ratio','M6S1S2_ratio',
                                           'M7S1S2_ratio','M8S1S2_ratio','M9S1S2_ratio','M10S1S2_ratio','M11S1S2_ratio','M12S1S2_ratio',
                                           'S1_return','S1_ratio','S2_return','S2_ratio','S1S2_ratio',
                                           'Trading Year','PairTrade','SP500Trade'
                                           ])

    print('% Complete:')
    ctr = 0
    for i in range(len(find_pairs_df)):
        ctr += 1
        print(100.0*ctr/len(find_pairs_df))
        for year_int in [1,2,3]:        
            Symbol1 = find_pairs_df['Symbol1'][i]
            Symbol2 = find_pairs_df['Symbol1'][i]

            MS1_returns =[float(sym_stats_df[(sym_stats_df['Symbol']==Symbol1) & (sym_stats_df['Trading Year']==year_int)]['M1_return']),
                          float(sym_stats_df[(sym_stats_df['Symbol']==Symbol1) & (sym_stats_df['Trading Year']==year_int)]['M2_return']),
                          float(sym_stats_df[(sym_stats_df['Symbol']==Symbol1) & (sym_stats_df['Trading Year']==year_int)]['M3_return']),
                          float(sym_stats_df[(sym_stats_df['Symbol']==Symbol1) & (sym_stats_df['Trading Year']==year_int)]['M4_return']),
                          float(sym_stats_df[(sym_stats_df['Symbol']==Symbol1) & (sym_stats_df['Trading Year']==year_int)]['M5_return']),
                          float(sym_stats_df[(sym_stats_df['Symbol']==Symbol1) & (sym_stats_df['Trading Year']==year_int)]['M6_return']),
                          float(sym_stats_df[(sym_stats_df['Symbol']==Symbol1) & (sym_stats_df['Trading Year']==year_int)]['M7_return']),
                          float(sym_stats_df[(sym_stats_df['Symbol']==Symbol1) & (sym_stats_df['Trading Year']==year_int)]['M8_return']),
                          float(sym_stats_df[(sym_stats_df['Symbol']==Symbol1) & (sym_stats_df['Trading Year']==year_int)]['M9_return']),
                          float(sym_stats_df[(sym_stats_df['Symbol']==Symbol1) & (sym_stats_df['Trading Year']==year_int)]['M10_return']),
                          float(sym_stats_df[(sym_stats_df['Symbol']==Symbol1) & (sym_stats_df['Trading Year']==year_int)]['M11_return']),
                          float(sym_stats_df[(sym_stats_df['Symbol']==Symbol1) & (sym_stats_df['Trading Year']==year_int)]['M12_return'])]

            MS1_ratios = [float(sym_stats_df[(sym_stats_df['Symbol']==Symbol1) & (sym_stats_df['Trading Year']==year_int)]['M1_ratio']),
                          float(sym_stats_df[(sym_stats_df['Symbol']==Symbol1) & (sym_stats_df['Trading Year']==year_int)]['M2_ratio']),
                          float(sym_stats_df[(sym_stats_df['Symbol']==Symbol1) & (sym_stats_df['Trading Year']==year_int)]['M3_ratio']),
                          float(sym_stats_df[(sym_stats_df['Symbol']==Symbol1) & (sym_stats_df['Trading Year']==year_int)]['M4_ratio']),
                          float(sym_stats_df[(sym_stats_df['Symbol']==Symbol1) & (sym_stats_df['Trading Year']==year_int)]['M5_ratio']),
                          float(sym_stats_df[(sym_stats_df['Symbol']==Symbol1) & (sym_stats_df['Trading Year']==year_int)]['M6_ratio']),
                          float(sym_stats_df[(sym_stats_df['Symbol']==Symbol1) & (sym_stats_df['Trading Year']==year_int)]['M7_ratio']),
                          float(sym_stats_df[(sym_stats_df['Symbol']==Symbol1) & (sym_stats_df['Trading Year']==year_int)]['M8_ratio']),
                          float(sym_stats_df[(sym_stats_df['Symbol']==Symbol1) & (sym_stats_df['Trading Year']==year_int)]['M9_ratio']),
                          float(sym_stats_df[(sym_stats_df['Symbol']==Symbol1) & (sym_stats_df['Trading Year']==year_int)]['M10_ratio']),
                          float(sym_stats_df[(sym_stats_df['Symbol']==Symbol1) & (sym_stats_df['Trading Year']==year_int)]['M11_ratio']),
                          float(sym_stats_df[(sym_stats_df['Symbol']==Symbol1) & (sym_stats_df['Trading Year']==year_int)]['M12_ratio'])]

            MS2_returns =[float(sym_stats_df[(sym_stats_df['Symbol']==Symbol2) & (sym_stats_df['Trading Year']==year_int)]['M1_return']),
                          float(sym_stats_df[(sym_stats_df['Symbol']==Symbol2) & (sym_stats_df['Trading Year']==year_int)]['M2_return']),
                          float(sym_stats_df[(sym_stats_df['Symbol']==Symbol2) & (sym_stats_df['Trading Year']==year_int)]['M3_return']),
                          float(sym_stats_df[(sym_stats_df['Symbol']==Symbol2) & (sym_stats_df['Trading Year']==year_int)]['M4_return']),
                          float(sym_stats_df[(sym_stats_df['Symbol']==Symbol2) & (sym_stats_df['Trading Year']==year_int)]['M5_return']),
                          float(sym_stats_df[(sym_stats_df['Symbol']==Symbol2) & (sym_stats_df['Trading Year']==year_int)]['M6_return']),
                          float(sym_stats_df[(sym_stats_df['Symbol']==Symbol2) & (sym_stats_df['Trading Year']==year_int)]['M7_return']),
                          float(sym_stats_df[(sym_stats_df['Symbol']==Symbol2) & (sym_stats_df['Trading Year']==year_int)]['M8_return']),
                          float(sym_stats_df[(sym_stats_df['Symbol']==Symbol2) & (sym_stats_df['Trading Year']==year_int)]['M9_return']),
                          float(sym_stats_df[(sym_stats_df['Symbol']==Symbol2) & (sym_stats_df['Trading Year']==year_int)]['M10_return']),
                          float(sym_stats_df[(sym_stats_df['Symbol']==Symbol2) & (sym_stats_df['Trading Year']==year_int)]['M11_return']),
                          float(sym_stats_df[(sym_stats_df['Symbol']==Symbol2) & (sym_stats_df['Trading Year']==year_int)]['M12_return'])]

            MS2_ratios = [float(sym_stats_df[(sym_stats_df['Symbol']==Symbol2) & (sym_stats_df['Trading Year']==year_int)]['M1_ratio']),
                          float(sym_stats_df[(sym_stats_df['Symbol']==Symbol2) & (sym_stats_df['Trading Year']==year_int)]['M2_ratio']),
                          float(sym_stats_df[(sym_stats_df['Symbol']==Symbol2) & (sym_stats_df['Trading Year']==year_int)]['M3_ratio']),
                          float(sym_stats_df[(sym_stats_df['Symbol']==Symbol2) & (sym_stats_df['Trading Year']==year_int)]['M4_ratio']),
                          float(sym_stats_df[(sym_stats_df['Symbol']==Symbol2) & (sym_stats_df['Trading Year']==year_int)]['M5_ratio']),
                          float(sym_stats_df[(sym_stats_df['Symbol']==Symbol2) & (sym_stats_df['Trading Year']==year_int)]['M6_ratio']),
                          float(sym_stats_df[(sym_stats_df['Symbol']==Symbol2) & (sym_stats_df['Trading Year']==year_int)]['M7_ratio']),
                          float(sym_stats_df[(sym_stats_df['Symbol']==Symbol2) & (sym_stats_df['Trading Year']==year_int)]['M8_ratio']),
                          float(sym_stats_df[(sym_stats_df['Symbol']==Symbol2) & (sym_stats_df['Trading Year']==year_int)]['M9_ratio']),
                          float(sym_stats_df[(sym_stats_df['Symbol']==Symbol2) & (sym_stats_df['Trading Year']==year_int)]['M10_ratio']),
                          float(sym_stats_df[(sym_stats_df['Symbol']==Symbol2) & (sym_stats_df['Trading Year']==year_int)]['M11_ratio']),
                          float(sym_stats_df[(sym_stats_df['Symbol']==Symbol2) & (sym_stats_df['Trading Year']==year_int)]['M12_ratio'])]

            S1_return = float(sym_stats_df[(sym_stats_df['Symbol']==Symbol1) & (sym_stats_df['Trading Year']==year_int)]['Return'])
            S1_ratio  = float(sym_stats_df[(sym_stats_df['Symbol']==Symbol1) & (sym_stats_df['Trading Year']==year_int)]['Ratio'])

            S2_return = float(sym_stats_df[(sym_stats_df['Symbol']==Symbol2) & (sym_stats_df['Trading Year']==year_int)]['Return'])
            S2_ratio  = float(sym_stats_df[(sym_stats_df['Symbol']==Symbol2) & (sym_stats_df['Trading Year']==year_int)]['Ratio'])

            train_set_df = train_set_df.append({'Symbol1':find_pairs_df['Symbol1'][i],'S1Sector':find_pairs_df['S1Sector'][i],'S1Industry':find_pairs_df['S1Industry'][i],
                                                'Symbol2':find_pairs_df['Symbol2'][i],'S2Sector':find_pairs_df['S2Sector'][i],'S2Industry':find_pairs_df['S2Industry'][i],
                                                'M1S1_return':MS1_returns[0],'M2S1_return':MS1_returns[1],'M3S1_return':MS1_returns[2],'M4S1_return':MS1_returns[3],
                                                'M5S1_return':MS1_returns[4],'M6S1_return':MS1_returns[5],'M7S1_return':MS1_returns[6],'M8S1_return':MS1_returns[7],
                                                'M9S1_return':MS1_returns[8],'M10S1_return':MS1_returns[9],'M11S1_return':MS1_returns[10],'M12S1_return':MS1_returns[11],
                                                'M1S1_ratio':MS1_ratios[0],'M2S1_ratio':MS1_ratios[1],'M3S1_ratio':MS1_ratios[2],'M4S1_ratio':MS1_ratios[3],
                                                'M5S1_ratio':MS1_ratios[4],'M6S1_ratio':MS1_ratios[5],'M7S1_ratio':MS1_ratios[6],'M8S1_ratio':MS1_ratios[7],
                                                'M9S1_ratio':MS1_ratios[8],'M10S1_ratio':MS1_ratios[9],'M11S1_ratio':MS1_ratios[10],'M12S1_ratio':MS1_ratios[11],
                                                'M1S2_return':MS2_returns[0],'M2S2_return':MS2_returns[1],'M3S2_return':MS2_returns[2],'M4S2_return':MS2_returns[3],
                                                'M5S2_return':MS2_returns[4],'M6S2_return':MS2_returns[5],'M7S2_return':MS2_returns[6],'M8S2_return':MS2_returns[7],
                                                'M9S2_return':MS2_returns[8],'M10S2_return':MS2_returns[9],'M11S2_return':MS2_returns[10],'M12S2_return':MS2_returns[11],
                                                'M1S2_ratio':MS2_ratios[0],'M2S2_ratio':MS2_ratios[1],'M3S2_ratio':MS2_ratios[2],'M4S2_ratio':MS2_ratios[3],
                                                'M5S2_ratio':MS2_ratios[4],'M6S2_ratio':MS2_ratios[5],'M7S2_ratio':MS2_ratios[6],'M8S2_ratio':MS2_ratios[7],
                                                'M9S2_ratio':MS2_ratios[8],'M10S2_ratio':MS2_ratios[9],'M11S2_ratio':MS2_ratios[10],'M12S2_ratio':MS2_ratios[11],
                                                'M1S1S2_ratio':MS1_returns[0]/MS2_returns[0],'M2S1S2_ratio':MS1_returns[1]/MS2_returns[1],'M3S1S2_ratio':MS1_returns[2]/MS2_returns[2],
                                                'M4S1S2_ratio':MS1_returns[3]/MS2_returns[3],'M5S1S2_ratio':MS1_returns[4]/MS2_returns[4],'M6S1S2_ratio':MS1_returns[5]/MS2_returns[5],
                                                'M7S1S2_ratio':MS1_returns[6]/MS2_returns[6],'M8S1S2_ratio':MS1_returns[7]/MS2_returns[7],'M9S1S2_ratio':MS1_returns[8]/MS2_returns[8],
                                                'M10S1S2_ratio':MS1_returns[9]/MS2_returns[9],'M11S1S2_ratio':MS1_returns[10]/MS2_returns[10],'M12S1S2_ratio':MS1_returns[11]/MS2_returns[11],
                                                'S1_return':S1_return,'S1_ratio':S1_ratio,'S2_return':S2_return,'S2_ratio':S2_ratio,'S1S2_ratio':S1_return/S2_return,
                                                'Trading Year':year_int,'PairTrade':find_pairs_df['PairTrade'+str(year_int)][i],'SP500Trade':find_pairs_df['SP500Trade'+str(year_int)][i]},
                                                ignore_index = True)

    train_set_df.to_csv('train_set_data.csv')

Dataframe already computed. Importing now.


In [10]:
#Add a one-hot encoded variable for successful/unsuccessful pairs

train_set_df['BeatMarket'] = list(map(lambda x: int(str(x).replace('True', '1').replace('False','0')), list(train_set_df['PairTrade'] > train_set_df['SP500Trade'])))


In [11]:
train_set_df


Symbol1           S1Sector             S1Industry Symbol2  \
0          AAL        Industrials               Airlines     APA   
1          AAL        Industrials               Airlines     APA   
2          AAL        Industrials               Airlines     APA   
3          UAA  Consumer Cyclical  Apparel Manufacturing     VTR   
4          UAA  Consumer Cyclical  Apparel Manufacturing     VTR   
...        ...                ...                    ...     ...   
368275    CTXS         Technology   Software—Application    ENPH   
368276    CTXS         Technology   Software—Application    ENPH   
368277    ENPH         Technology                  Solar      KR   
368278    ENPH         Technology                  Solar      KR   
368279    ENPH         Technology                  Solar      KR   

                  S2Sector                  S2Industry  M1S1_return  \
0                   Energy               Oil & Gas E&P     0.991863   
1                   Energy               Oil & Gas E&P     0.882048   
2                   Energy               Oil & Gas E&P     1.041041   
3              Real Estate  REIT—Healthcare Facilities     0.722589   
4              Real Estate  REIT—Healthcare Facilities     1.266229   
...                    ...                         ...          ...   
368275          Technology                       Solar     0.994765   
368276          Technology                       Solar     0.983923   
368277  Consumer Defensive              Grocery Stores     0.976190   
368278  Consumer Defensive              Grocery Stores     1.461140   
368279  Consumer Defensive              Grocery Stores     1.180556   

        M2S1_return  M3S1_return  M4S1_return  ...  M12S1S2_ratio  S1_return  \
0          0.890882     1.038644     1.016265  ...            1.0   1.241415   
1          1.079836     0.853450     0.914821  ...            1.0   0.585396   
2          0.883814     1.091111     0.933478  ...            1.0   0.851687   
3          0.893911     0.985552     0.990042  ...            1.0   0.452444   
4          0.931315     0.996283     1.245050  ...            1.0   1.494530   
...             ...          ...          ...  ...            ...        ...   
368275     1.039925     1.030637     1.075557  ...            1.0   1.189778   
368276     0.949614     0.988936     0.961365  ...            1.0   1.098336   
368277     0.848485     0.906475     0.530303  ...            1.0   1.154762   
368278     1.712230     0.962185     1.221968  ...            1.0   3.383420   
368279     1.212682     1.033917     1.553552  ...            1.0   4.861111   

        S1_ratio  S2_return  S2_ratio  S1S2_ratio  Trading Year   PairTrade  \
0       1.530763   1.241415  1.530763         1.0             1  153.156120   
1       0.557847   0.585396  0.557847         1.0             2  155.414642   
2       1.066939   0.851687  1.066939         1.0             3  240.999797   
3       0.557899   0.452444  0.557899         1.0             1  128.047603   
4       1.424197   1.494530  1.424197         1.0             2  139.914720   
...          ...        ...       ...         ...           ...         ...   
368275  1.133787   1.189778  1.133787         1.0             2  -79.649702   
368276  1.375924   1.098336  1.375924         1.0             3 -260.580727   
368277  1.423913   1.154762  1.423913         1.0             1  -30.435064   
368278  3.224196   3.383420  3.224196         1.0             2  -85.439827   
368279  6.089686   4.861111  6.089686         1.0             3 -280.709603   

        SP500Trade  BeatMarket  
0        94.600368           1  
1       125.049290           1  
2       114.082979           1  
3        94.600368           1  
4       125.049290           1  
...            ...         ...  
368275  125.049290           0  
368276  114.082979           0  
368277   94.600368           0  
368278  125.049290           0  
368279  114.082979           0  

[368280 rows x 75 columns]

In [12]:
if os.path.isfile('test_set_data.csv'):
    print('Dataframe already computed. Importing now.')
    test_set_df = pd.read_csv('test_set_data.csv').drop('Unnamed: 0',1)
else:
    test_set_df = pd.DataFrame(columns = ['Symbol1','S1Sector','S1Industry','Symbol2','S2Sector','S2Industry',
                                           'M1S1_return','M2S1_return','M3S1_return','M4S1_return', 'M5S1_return', 'M6S1_return',
                                           'M7S1_return','M8S1_return','M9S1_return','M10S1_return','M11S1_return','M12S1_return',
                                           'M1S1_ratio', 'M2S1_ratio', 'M3S1_ratio', 'M4S1_ratio',  'M5S1_ratio',  'M6S1_ratio',
                                           'M7S1_ratio', 'M8S1_ratio', 'M9S1_ratio', 'M10S1_ratio', 'M11S1_ratio', 'M12S1_ratio',
                                           'M1S2_return','M2S2_return','M3S2_return','M4S2_return', 'M5S2_return', 'M6S2_return',
                                           'M7S2_return','M8S2_return','M9S2_return','M10S2_return','M11S2_return','M12S2_return',
                                           'M1S2_ratio', 'M2S2_ratio', 'M3S2_ratio', 'M4S2_ratio',  'M5S2_ratio',  'M6S2_ratio',
                                           'M7S2_ratio', 'M8S2_ratio', 'M9S2_ratio', 'M10S2_ratio', 'M11S2_ratio', 'M12S2_ratio',
                                           'M1S1S2_ratio','M2S1S2_ratio','M3S1S2_ratio','M4S1S2_ratio','M5S1S2_ratio','M6S1S2_ratio',
                                           'M7S1S2_ratio','M8S1S2_ratio','M9S1S2_ratio','M10S1S2_ratio','M11S1S2_ratio','M12S1S2_ratio',
                                           'S1_return','S1_ratio','S2_return','S2_ratio','S1S2_ratio'
                                           ])

    print('% Complete:')
    ctr = 0
    for i in range(len(find_pairs_df)):
        ctr += 1
        print(100.0*ctr/len(find_pairs_df))
        for year_int in [4]:        
            Symbol1 = find_pairs_df['Symbol1'][i]
            Symbol2 = find_pairs_df['Symbol1'][i]

            MS1_returns =[float(sym_stats_df[(sym_stats_df['Symbol']==Symbol1) & (sym_stats_df['Trading Year']==year_int)]['M1_return']),
                          float(sym_stats_df[(sym_stats_df['Symbol']==Symbol1) & (sym_stats_df['Trading Year']==year_int)]['M2_return']),
                          float(sym_stats_df[(sym_stats_df['Symbol']==Symbol1) & (sym_stats_df['Trading Year']==year_int)]['M3_return']),
                          float(sym_stats_df[(sym_stats_df['Symbol']==Symbol1) & (sym_stats_df['Trading Year']==year_int)]['M4_return']),
                          float(sym_stats_df[(sym_stats_df['Symbol']==Symbol1) & (sym_stats_df['Trading Year']==year_int)]['M5_return']),
                          float(sym_stats_df[(sym_stats_df['Symbol']==Symbol1) & (sym_stats_df['Trading Year']==year_int)]['M6_return']),
                          float(sym_stats_df[(sym_stats_df['Symbol']==Symbol1) & (sym_stats_df['Trading Year']==year_int)]['M7_return']),
                          float(sym_stats_df[(sym_stats_df['Symbol']==Symbol1) & (sym_stats_df['Trading Year']==year_int)]['M8_return']),
                          float(sym_stats_df[(sym_stats_df['Symbol']==Symbol1) & (sym_stats_df['Trading Year']==year_int)]['M9_return']),
                          float(sym_stats_df[(sym_stats_df['Symbol']==Symbol1) & (sym_stats_df['Trading Year']==year_int)]['M10_return']),
                          float(sym_stats_df[(sym_stats_df['Symbol']==Symbol1) & (sym_stats_df['Trading Year']==year_int)]['M11_return']),
                          float(sym_stats_df[(sym_stats_df['Symbol']==Symbol1) & (sym_stats_df['Trading Year']==year_int)]['M12_return'])]

            MS1_ratios = [float(sym_stats_df[(sym_stats_df['Symbol']==Symbol1) & (sym_stats_df['Trading Year']==year_int)]['M1_ratio']),
                          float(sym_stats_df[(sym_stats_df['Symbol']==Symbol1) & (sym_stats_df['Trading Year']==year_int)]['M2_ratio']),
                          float(sym_stats_df[(sym_stats_df['Symbol']==Symbol1) & (sym_stats_df['Trading Year']==year_int)]['M3_ratio']),
                          float(sym_stats_df[(sym_stats_df['Symbol']==Symbol1) & (sym_stats_df['Trading Year']==year_int)]['M4_ratio']),
                          float(sym_stats_df[(sym_stats_df['Symbol']==Symbol1) & (sym_stats_df['Trading Year']==year_int)]['M5_ratio']),
                          float(sym_stats_df[(sym_stats_df['Symbol']==Symbol1) & (sym_stats_df['Trading Year']==year_int)]['M6_ratio']),
                          float(sym_stats_df[(sym_stats_df['Symbol']==Symbol1) & (sym_stats_df['Trading Year']==year_int)]['M7_ratio']),
                          float(sym_stats_df[(sym_stats_df['Symbol']==Symbol1) & (sym_stats_df['Trading Year']==year_int)]['M8_ratio']),
                          float(sym_stats_df[(sym_stats_df['Symbol']==Symbol1) & (sym_stats_df['Trading Year']==year_int)]['M9_ratio']),
                          float(sym_stats_df[(sym_stats_df['Symbol']==Symbol1) & (sym_stats_df['Trading Year']==year_int)]['M10_ratio']),
                          float(sym_stats_df[(sym_stats_df['Symbol']==Symbol1) & (sym_stats_df['Trading Year']==year_int)]['M11_ratio']),
                          float(sym_stats_df[(sym_stats_df['Symbol']==Symbol1) & (sym_stats_df['Trading Year']==year_int)]['M12_ratio'])]

            MS2_returns =[float(sym_stats_df[(sym_stats_df['Symbol']==Symbol2) & (sym_stats_df['Trading Year']==year_int)]['M1_return']),
                          float(sym_stats_df[(sym_stats_df['Symbol']==Symbol2) & (sym_stats_df['Trading Year']==year_int)]['M2_return']),
                          float(sym_stats_df[(sym_stats_df['Symbol']==Symbol2) & (sym_stats_df['Trading Year']==year_int)]['M3_return']),
                          float(sym_stats_df[(sym_stats_df['Symbol']==Symbol2) & (sym_stats_df['Trading Year']==year_int)]['M4_return']),
                          float(sym_stats_df[(sym_stats_df['Symbol']==Symbol2) & (sym_stats_df['Trading Year']==year_int)]['M5_return']),
                          float(sym_stats_df[(sym_stats_df['Symbol']==Symbol2) & (sym_stats_df['Trading Year']==year_int)]['M6_return']),
                          float(sym_stats_df[(sym_stats_df['Symbol']==Symbol2) & (sym_stats_df['Trading Year']==year_int)]['M7_return']),
                          float(sym_stats_df[(sym_stats_df['Symbol']==Symbol2) & (sym_stats_df['Trading Year']==year_int)]['M8_return']),
                          float(sym_stats_df[(sym_stats_df['Symbol']==Symbol2) & (sym_stats_df['Trading Year']==year_int)]['M9_return']),
                          float(sym_stats_df[(sym_stats_df['Symbol']==Symbol2) & (sym_stats_df['Trading Year']==year_int)]['M10_return']),
                          float(sym_stats_df[(sym_stats_df['Symbol']==Symbol2) & (sym_stats_df['Trading Year']==year_int)]['M11_return']),
                          float(sym_stats_df[(sym_stats_df['Symbol']==Symbol2) & (sym_stats_df['Trading Year']==year_int)]['M12_return'])]

            MS2_ratios = [float(sym_stats_df[(sym_stats_df['Symbol']==Symbol2) & (sym_stats_df['Trading Year']==year_int)]['M1_ratio']),
                          float(sym_stats_df[(sym_stats_df['Symbol']==Symbol2) & (sym_stats_df['Trading Year']==year_int)]['M2_ratio']),
                          float(sym_stats_df[(sym_stats_df['Symbol']==Symbol2) & (sym_stats_df['Trading Year']==year_int)]['M3_ratio']),
                          float(sym_stats_df[(sym_stats_df['Symbol']==Symbol2) & (sym_stats_df['Trading Year']==year_int)]['M4_ratio']),
                          float(sym_stats_df[(sym_stats_df['Symbol']==Symbol2) & (sym_stats_df['Trading Year']==year_int)]['M5_ratio']),
                          float(sym_stats_df[(sym_stats_df['Symbol']==Symbol2) & (sym_stats_df['Trading Year']==year_int)]['M6_ratio']),
                          float(sym_stats_df[(sym_stats_df['Symbol']==Symbol2) & (sym_stats_df['Trading Year']==year_int)]['M7_ratio']),
                          float(sym_stats_df[(sym_stats_df['Symbol']==Symbol2) & (sym_stats_df['Trading Year']==year_int)]['M8_ratio']),
                          float(sym_stats_df[(sym_stats_df['Symbol']==Symbol2) & (sym_stats_df['Trading Year']==year_int)]['M9_ratio']),
                          float(sym_stats_df[(sym_stats_df['Symbol']==Symbol2) & (sym_stats_df['Trading Year']==year_int)]['M10_ratio']),
                          float(sym_stats_df[(sym_stats_df['Symbol']==Symbol2) & (sym_stats_df['Trading Year']==year_int)]['M11_ratio']),
                          float(sym_stats_df[(sym_stats_df['Symbol']==Symbol2) & (sym_stats_df['Trading Year']==year_int)]['M12_ratio'])]

            S1_return = float(sym_stats_df[(sym_stats_df['Symbol']==Symbol1) & (sym_stats_df['Trading Year']==year_int)]['Return'])
            S1_ratio  = float(sym_stats_df[(sym_stats_df['Symbol']==Symbol1) & (sym_stats_df['Trading Year']==year_int)]['Ratio'])

            S2_return = float(sym_stats_df[(sym_stats_df['Symbol']==Symbol2) & (sym_stats_df['Trading Year']==year_int)]['Return'])
            S2_ratio  = float(sym_stats_df[(sym_stats_df['Symbol']==Symbol2) & (sym_stats_df['Trading Year']==year_int)]['Ratio'])

            test_set_df = test_set_df.append({'Symbol1':find_pairs_df['Symbol1'][i],'S1Sector':find_pairs_df['S1Sector'][i],'S1Industry':find_pairs_df['S1Industry'][i],
                                                'Symbol2':find_pairs_df['Symbol2'][i],'S2Sector':find_pairs_df['S2Sector'][i],'S2Industry':find_pairs_df['S2Industry'][i],
                                                'M1S1_return':MS1_returns[0],'M2S1_return':MS1_returns[1],'M3S1_return':MS1_returns[2],'M4S1_return':MS1_returns[3],
                                                'M5S1_return':MS1_returns[4],'M6S1_return':MS1_returns[5],'M7S1_return':MS1_returns[6],'M8S1_return':MS1_returns[7],
                                                'M9S1_return':MS1_returns[8],'M10S1_return':MS1_returns[9],'M11S1_return':MS1_returns[10],'M12S1_return':MS1_returns[11],
                                                'M1S1_ratio':MS1_ratios[0],'M2S1_ratio':MS1_ratios[1],'M3S1_ratio':MS1_ratios[2],'M4S1_ratio':MS1_ratios[3],
                                                'M5S1_ratio':MS1_ratios[4],'M6S1_ratio':MS1_ratios[5],'M7S1_ratio':MS1_ratios[6],'M8S1_ratio':MS1_ratios[7],
                                                'M9S1_ratio':MS1_ratios[8],'M10S1_ratio':MS1_ratios[9],'M11S1_ratio':MS1_ratios[10],'M12S1_ratio':MS1_ratios[11],
                                                'M1S2_return':MS2_returns[0],'M2S2_return':MS2_returns[1],'M3S2_return':MS2_returns[2],'M4S2_return':MS2_returns[3],
                                                'M5S2_return':MS2_returns[4],'M6S2_return':MS2_returns[5],'M7S2_return':MS2_returns[6],'M8S2_return':MS2_returns[7],
                                                'M9S2_return':MS2_returns[8],'M10S2_return':MS2_returns[9],'M11S2_return':MS2_returns[10],'M12S2_return':MS2_returns[11],
                                                'M1S2_ratio':MS2_ratios[0],'M2S2_ratio':MS2_ratios[1],'M3S2_ratio':MS2_ratios[2],'M4S2_ratio':MS2_ratios[3],
                                                'M5S2_ratio':MS2_ratios[4],'M6S2_ratio':MS2_ratios[5],'M7S2_ratio':MS2_ratios[6],'M8S2_ratio':MS2_ratios[7],
                                                'M9S2_ratio':MS2_ratios[8],'M10S2_ratio':MS2_ratios[9],'M11S2_ratio':MS2_ratios[10],'M12S2_ratio':MS2_ratios[11],
                                                'M1S1S2_ratio':MS1_returns[0]/MS2_returns[0],'M2S1S2_ratio':MS1_returns[1]/MS2_returns[1],'M3S1S2_ratio':MS1_returns[2]/MS2_returns[2],
                                                'M4S1S2_ratio':MS1_returns[3]/MS2_returns[3],'M5S1S2_ratio':MS1_returns[4]/MS2_returns[4],'M6S1S2_ratio':MS1_returns[5]/MS2_returns[5],
                                                'M7S1S2_ratio':MS1_returns[6]/MS2_returns[6],'M8S1S2_ratio':MS1_returns[7]/MS2_returns[7],'M9S1S2_ratio':MS1_returns[8]/MS2_returns[8],
                                                'M10S1S2_ratio':MS1_returns[9]/MS2_returns[9],'M11S1S2_ratio':MS1_returns[10]/MS2_returns[10],'M12S1S2_ratio':MS1_returns[11]/MS2_returns[11],
                                                'S1_return':S1_return,'S1_ratio':S1_ratio,'S2_return':S2_return,'S2_ratio':S2_ratio,'S1S2_ratio':S1_return/S2_return,
                                                'Trading Year':year_int},
                                                ignore_index = True)

    test_set_df.to_csv('test_set_data.csv')
    

Dataframe already computed. Importing now.


In [13]:
#Need to do a stratified train/test split
pairs_train, pairs_validation = train_test_split(train_set_df.copy(), shuffle=True, random_state=2311,
                                           stratify=train_set_df[['Trading Year','BeatMarket']], test_size=0.2 )


In [14]:
#Define initial classifiers to be deep copied in subsequent fit iterations
extratrees = ExtraTreesClassifier(n_estimators=500, max_depth=250, random_state=2311)
randomforest = RandomForestClassifier(n_estimators=500, max_depth=250, random_state=2311)
log_reg = LogisticRegression(max_iter=500000)
LDA = LinearDiscriminantAnalysis()
QDA = QuadraticDiscriminantAnalysis()
nb = GaussianNB()


def FitClassifier(classifier,use_features):
    classifier_clone = clone(classifier)
    classifier_clone.fit( pairs_train[use_features], pairs_train['BeatMarket'] )

    train_preds = classifier_clone.predict(pairs_train[use_features])
    print( "Training accuracy:",100.0*accuracy_score(pairs_train['BeatMarket'], train_preds) )

    val_preds = classifier_clone.predict(pairs_validation[use_features])
    print( "Validation accuracy:",100.0*accuracy_score(pairs_validation['BeatMarket'], val_preds) )


In [15]:
check_features =[ ['M1S1_return','M2S1_return','M3S1_return','M4S1_return','M5S1_return','M6S1_return',
                'M7S1_return','M8S1_return', 'M9S1_return', 'M10S1_return','M11S1_return','M12S1_return',
                'M1S1_ratio','M2S1_ratio','M3S1_ratio','M4S1_ratio','M5S1_ratio','M6S1_ratio','M7S1_ratio',
                'M8S1_ratio','M9S1_ratio','M10S1_ratio','M11S1_ratio','M12S1_ratio','M1S2_return',
                'M2S2_return','M3S2_return','M4S2_return','M5S2_return','M6S2_return','M7S2_return',
                'M8S2_return','M9S2_return','M10S2_return','M11S2_return','M12S2_return','M1S2_ratio',
                'M2S2_ratio','M3S2_ratio','M4S2_ratio','M5S2_ratio','M6S2_ratio','M7S2_ratio','M8S2_ratio',
                'M9S2_ratio','M10S2_ratio','M11S2_ratio','M12S2_ratio','M1S1S2_ratio','M2S1S2_ratio',
                'M3S1S2_ratio','M4S1S2_ratio','M5S1S2_ratio','M6S1S2_ratio','M7S1S2_ratio','M8S1S2_ratio',
                'M9S1S2_ratio','M10S1S2_ratio','M11S1S2_ratio','M12S1S2_ratio',
                'S1_return','S1_ratio','S2_return','S2_ratio','S1S2_ratio'],
                
                ['M1S1_return','M2S1_return','M3S1_return','M4S1_return','M5S1_return','M6S1_return',
                'M7S1_return','M8S1_return', 'M9S1_return', 'M10S1_return','M11S1_return','M12S1_return',
                'M1S1_ratio','M2S1_ratio','M3S1_ratio','M4S1_ratio','M5S1_ratio','M6S1_ratio','M7S1_ratio',
                'M8S1_ratio','M9S1_ratio','M10S1_ratio','M11S1_ratio','M12S1_ratio','M1S2_return',
                'M2S2_return','M3S2_return','M4S2_return','M5S2_return','M6S2_return','M7S2_return',
                'M8S2_return','M9S2_return','M10S2_return','M11S2_return','M12S2_return','M1S2_ratio',
                'M2S2_ratio','M3S2_ratio','M4S2_ratio','M5S2_ratio','M6S2_ratio','M7S2_ratio','M8S2_ratio',
                'M9S2_ratio','M10S2_ratio','M11S2_ratio','M12S2_ratio','M1S1S2_ratio','M2S1S2_ratio',
                'M3S1S2_ratio','M4S1S2_ratio','M5S1S2_ratio','M6S1S2_ratio','M7S1S2_ratio','M8S1S2_ratio',
                'M9S1S2_ratio','M10S1S2_ratio','M11S1S2_ratio','M12S1S2_ratio'],
                
                ['M1S1S2_ratio','M2S1S2_ratio','M3S1S2_ratio','M4S1S2_ratio','M5S1S2_ratio','M6S1S2_ratio',
                'M7S1S2_ratio','M8S1S2_ratio','M9S1S2_ratio','M10S1S2_ratio','M11S1S2_ratio','M12S1S2_ratio',
                'S1_return','S1_ratio','S2_return','S2_ratio','S1S2_ratio'],

                ['S1_return','S1_ratio','S2_return','S2_ratio','S1S2_ratio'],

                ['S1S2_ratio'] ]


In [16]:
for use_features in check_features:
    print('Using the features in check_features['+str(check_features.index(use_features))+']')
    print("Extra Trees:")
    try:
        FitClassifier(extratrees,use_features)
    except:
        print()
    print("Random Forest:")
    try:
        FitClassifier(randomforest,use_features)
    except:
        print()
    print("Logistic Regression:")
    try:
        FitClassifier(log_reg,use_features)
    except:
        print()
    print("LDA:")
    try:
        FitClassifier(LDA,use_features)
    except:
        print()
    print("QDA:")
    try:
        FitClassifier(QDA,use_features)
    except:
        print()
    print("Naive Bayes:")
    try:
        FitClassifier(nb,use_features)
    except:
        print()
    print()


Using the features in check_features[0]
Extra Trees:
Training accuracy: 82.03099543825351
Validation accuracy: 82.01096991419573
Random Forest:
Training accuracy: 82.03065602259151
Validation accuracy: 82.00418160095579
Logistic Regression:
Training accuracy: 79.97685185185185
Validation accuracy: 79.97040295427392
LDA:
Training accuracy: 79.97685185185185
Validation accuracy: 79.97040295427392
QDA:


/Users/vallely.7/.conda/envs/python/lib/python3.8/site-packages/sklearn/discriminant_analysis.py:878: UserWarning: Variables are collinear
  warnings.warn("Variables are collinear")


Training accuracy: 69.39488975779298
Validation accuracy: 69.5503421309873
Naive Bayes:
Training accuracy: 67.0311990876507
Validation accuracy: 67.1323449549256

Using the features in check_features[1]
Extra Trees:
Training accuracy: 82.03099543825351
Validation accuracy: 82.01096991419573
Random Forest:
Training accuracy: 82.03065602259151
Validation accuracy: 82.00418160095579
Logistic Regression:
Training accuracy: 79.97685185185185
Validation accuracy: 79.97040295427392
LDA:
Training accuracy: 79.97685185185185
Validation accuracy: 79.97040295427392
QDA:


/Users/vallely.7/.conda/envs/python/lib/python3.8/site-packages/sklearn/discriminant_analysis.py:878: UserWarning: Variables are collinear
  warnings.warn("Variables are collinear")


Training accuracy: 56.73095199304877
Validation accuracy: 56.68105789073531
Naive Bayes:
Training accuracy: 68.83112034321712
Validation accuracy: 68.64070815683719

Using the features in check_features[2]
Extra Trees:
Training accuracy: 82.03099543825351
Validation accuracy: 82.01096991419573
Random Forest:
Training accuracy: 82.03065602259151
Validation accuracy: 82.00418160095579
Logistic Regression:
Training accuracy: 68.61253665689149
Validation accuracy: 68.63256218094928
LDA:
Training accuracy: 68.56230313891605
Validation accuracy: 68.57146736178994
QDA:


...

Training accuracy: 69.03341207776693
Validation accuracy: 69.03307266210493
Naive Bayes:
Training accuracy: 63.01048115564245
Validation accuracy: 63.277940697295534

Using the features in check_features[3]
Extra Trees:
Training accuracy: 82.03099543825351
Validation accuracy: 82.01096991419573
Random Forest:
Training accuracy: 82.03065602259151
Validation accuracy: 82.00418160095579
Logistic Regression:
Training accuracy: 68.61253665689149
Validation accuracy: 68.63256218094928
LDA:
Training accuracy: 68.56230313891605
Validation accuracy: 68.57146736178994
QDA:
Training accuracy: 69.03341207776693


/Users/vallely.7/.conda/envs/python/lib/python3.8/site-packages/sklearn/discriminant_analysis.py:878: UserWarning: Variables are collinear
  warnings.warn("Variables are collinear")
/Users/vallely.7/.conda/envs/python/lib/python3.8/site-packages/sklearn/discriminant_analysis.py:903: RuntimeWarning: divide by zero encountered in power
  X2 = np.dot(Xm, R * (S ** (-0.5)))
/Users/vallely.7/.conda/envs/python/lib/python3.8/site-packages/sklearn/discriminant_analysis.py:903: RuntimeWarning: invalid value encountered in multiply
  X2 = np.dot(Xm, R * (S ** (-0.5)))
/Users/vallely.7/.conda/envs/python/lib/python3.8/site-packages/sklearn/discriminant_analysis.py:906: RuntimeWarning: divide by zero encountered in log
  u = np.asarray([np.sum(np.log(s)) for s in self.scalings_])
/Users/vallely.7/.conda/envs/python/lib/python3.8/site-packages/sklearn/discriminant_analysis.py:903: RuntimeWarning: divide by zero encountered in power
  X2 = np.dot(Xm, R * (S ** (-0.5)))
/Users/vallely.7/.conda/envs/

Validation accuracy: 69.03307266210493
Naive Bayes:
Training accuracy: 63.01048115564245
Validation accuracy: 63.277940697295534

Using the features in check_features[4]
Extra Trees:
Training accuracy: 69.03341207776693
Validation accuracy: 69.03307266210493
Random Forest:
Training accuracy: 69.03341207776693
Validation accuracy: 69.03307266210493
Logistic Regression:
Training accuracy: 69.03341207776693
Validation accuracy: 69.03307266210493
LDA:

QDA:
Training accuracy: 69.03341207776693
Validation accuracy: 69.03307266210493
Naive Bayes:


/Users/vallely.7/.conda/envs/python/lib/python3.8/site-packages/sklearn/discriminant_analysis.py:878: UserWarning: Variables are collinear
  warnings.warn("Variables are collinear")
/Users/vallely.7/.conda/envs/python/lib/python3.8/site-packages/sklearn/discriminant_analysis.py:903: RuntimeWarning: divide by zero encountered in power
  X2 = np.dot(Xm, R * (S ** (-0.5)))
/Users/vallely.7/.conda/envs/python/lib/python3.8/site-packages/sklearn/discriminant_analysis.py:906: RuntimeWarning: divide by zero encountered in log
  u = np.asarray([np.sum(np.log(s)) for s in self.scalings_])
/Users/vallely.7/.conda/envs/python/lib/python3.8/site-packages/sklearn/discriminant_analysis.py:903: RuntimeWarning: divide by zero encountered in power
  X2 = np.dot(Xm, R * (S ** (-0.5)))
/Users/vallely.7/.conda/envs/python/lib/python3.8/site-packages/sklearn/discriminant_analysis.py:906: RuntimeWarning: divide by zero encountered in log
  u = np.asarray([np.sum(np.log(s)) for s in self.scalings_])
/Users/v

Training accuracy: 69.03341207776693
Validation accuracy: 69.03307266210493



In [17]:
#Okay, these seems like a reasonable set of features to use for each classifier based on the above results

extratrees_features = check_features[2]
randomforest_features = check_features[2]
log_reg_features = check_features[1]
LDA_features = check_features[1]
QDA_features = check_features[0]
nb_features = check_features[1]


In [18]:
print("Final Classifiers:")
print()

print("Extra Trees:")
extratrees_final = clone(extratrees)
extratrees_final.fit( pairs_train[extratrees_features], pairs_train['BeatMarket'] )
train_preds = extratrees_final.predict(pairs_train[extratrees_features])
print( "Training accuracy:",100.0*accuracy_score(pairs_train['BeatMarket'], train_preds) )
val_preds = extratrees_final.predict(pairs_validation[extratrees_features])
print( "Validation accuracy:",100.0*accuracy_score(pairs_validation['BeatMarket'], val_preds) )
print()

print("Random Forest:")
randomforest_final = clone(randomforest)
randomforest_final.fit( pairs_train[randomforest_features], pairs_train['BeatMarket'] )
train_preds = randomforest_final.predict(pairs_train[randomforest_features])
print( "Training accuracy:",100.0*accuracy_score(pairs_train['BeatMarket'], train_preds) )
val_preds = randomforest_final.predict(pairs_validation[randomforest_features])
print( "Validation accuracy:",100.0*accuracy_score(pairs_validation['BeatMarket'], val_preds) )
print()

print("Logistic Regression:")
log_reg_final = clone(log_reg)
log_reg_final.fit( pairs_train[log_reg_features], pairs_train['BeatMarket'] )
train_preds = log_reg_final.predict(pairs_train[log_reg_features])
print( "Training accuracy:",100.0*accuracy_score(pairs_train['BeatMarket'], train_preds) )
val_preds = log_reg_final.predict(pairs_validation[log_reg_features])
print( "Validation accuracy:",100.0*accuracy_score(pairs_validation['BeatMarket'], val_preds) )
print()

print("LDA:")
LDA_final = clone(LDA)
LDA_final.fit( pairs_train[LDA_features], pairs_train['BeatMarket'] )
train_preds = LDA_final.predict(pairs_train[LDA_features])
print( "Training accuracy:",100.0*accuracy_score(pairs_train['BeatMarket'], train_preds) )
val_preds = LDA_final.predict(pairs_validation[LDA_features])
print( "Validation accuracy:",100.0*accuracy_score(pairs_validation['BeatMarket'], val_preds) )
print()

print("QDA:")
QDA_final = clone(QDA)
QDA_final.fit( pairs_train[QDA_features], pairs_train['BeatMarket'] )
train_preds = QDA_final.predict(pairs_train[QDA_features])
print( "Training accuracy:",100.0*accuracy_score(pairs_train['BeatMarket'], train_preds) )
val_preds = QDA_final.predict(pairs_validation[QDA_features])
print( "Validation accuracy:",100.0*accuracy_score(pairs_validation['BeatMarket'], val_preds) )
print()

print("Naive Bayes:")
nb_final = clone(nb)
QDA_final.fit( pairs_train[QDA_features], pairs_train['BeatMarket'] )
train_preds = QDA_final.predict(pairs_train[QDA_features])
print( "Training accuracy:",100.0*accuracy_score(pairs_train['BeatMarket'], train_preds) )
val_preds = QDA_final.predict(pairs_validation[QDA_features])
print( "Validation accuracy:",100.0*accuracy_score(pairs_validation['BeatMarket'], val_preds) )
print()


Final Classifiers:

Extra Trees:
Training accuracy: 82.03099543825351
Validation accuracy: 82.01096991419573

Random Forest:
Training accuracy: 82.03065602259151
Validation accuracy: 82.00418160095579

Logistic Regression:
Training accuracy: 79.97685185185185
Validation accuracy: 79.97040295427392

LDA:
Training accuracy: 79.97685185185185
Validation accuracy: 79.97040295427392

QDA:


/Users/vallely.7/.conda/envs/python/lib/python3.8/site-packages/sklearn/discriminant_analysis.py:878: UserWarning: Variables are collinear
  warnings.warn("Variables are collinear")


Training accuracy: 69.39488975779298
Validation accuracy: 69.5503421309873

Naive Bayes:


/Users/vallely.7/.conda/envs/python/lib/python3.8/site-packages/sklearn/discriminant_analysis.py:878: UserWarning: Variables are collinear
  warnings.warn("Variables are collinear")


Training accuracy: 69.39488975779298
Validation accuracy: 69.5503421309873



In [19]:
voting_features = check_features[0]

voting_soft = VotingClassifier( [('extratrees',clone(extratrees)), ('randomforest',clone(randomforest)),
                                 ('log_reg', clone(log_reg)),('LDA', clone(LDA)),('QDA', clone(QDA)),
                                 ('nb', clone(nb))], voting='soft' )

voting_soft.fit( pairs_train[voting_features], pairs_train['BeatMarket'] )

print("Voting (Soft):")
train_preds = voting_soft.predict(pairs_train[voting_features])
print( "Training accuracy:",100.0*accuracy_score(pairs_train['BeatMarket'], train_preds) )
val_preds = voting_soft.predict(pairs_validation[voting_features])
print( "Validation accuracy:",100.0*accuracy_score(pairs_validation['BeatMarket'], val_preds) )
print()


/Users/vallely.7/.conda/envs/python/lib/python3.8/site-packages/sklearn/discriminant_analysis.py:878: UserWarning: Variables are collinear
  warnings.warn("Variables are collinear")


Voting (Soft):
Training accuracy: 80.66382915173239
Validation accuracy: 80.62343868795482



In [20]:
#get predictions from the best classifier, which happens to be extra trees
final_preds = extratrees_final.predict(test_set_df[extratrees_features])
final_probs = extratrees_final.predict_proba(test_set_df[extratrees_features])


In [21]:
f = open("LikelyPairStocks_ML.txt", "w")
print("Symbol1\tSymbol2\tLast Avg. Diff.\t\tLast S1 Mean\t\tLast S2 Mean\t\tAvg. Ratio")
f.write("\tSymbol1\t\tSymbol2\t\tPairTrade\tSymbol1Trade\tSymbol2Trade\tSP500Trade"+"\n")
for i in range(len(find_pairs_df)):
    if final_preds[i] == 1:
        printstr =  find_pairs_df['Symbol1'][i]+'\t'+find_pairs_df['Symbol2'][i]+'\t'+str(find_pairs_df['LastAvgDiff'][i])+'\t'+str(find_pairs_df['LastSymbol1Mean'][i])+'\t'+str(find_pairs_df['LastSymbol2Mean'][i])+'\t'+str(round(find_pairs_df['MeanPairsRatio'][i],1))+'%'
        print(printstr)
        f.write(printstr+"\n")
f.close()

Symbol1	Symbol2	Last Avg. Diff.		Last S1 Mean		Last S2 Mean		Avg. Ratio
BKR	WYNN	-3.5385594410363554e-18	21.820666073802933	121.0017433318484	154.1%
DLTR	RHI	3.538559441036356e-17	103.14386448347236	56.67961692050159	151.5%
BKNG	DLTR	-6.015551049761804e-17	1889.627931146508	103.14386448347236	151.0%
CHRW	NVR	7.077118882072711e-18	79.7344851246868	3338.889723333229	148.1%
DLTR	WAB	-2.0346716785959045e-17	103.14386448347236	71.26423775722306	146.8%
DLTR	NTRS	8.138686714383618e-17	103.14386448347236	88.56184068049093	145.8%
FB	ROK	-1.2561886015679063e-16	185.3225893423377	164.84379735695887	145.3%
ANET	ROST	-5.661695105658169e-17	61.71735049243942	101.61178236273656	141.2%
LUMN	WDC	9.200254546694524e-17	11.18029068190738	50.43285378991845	141.0%
HOLX	URI	3.848183392127037e-17	48.18812769247716	131.56992054365546	140.7%
PSA	WDC	5.661695105658169e-17	210.64650632090775	50.43285378991845	140.5%
DLTR	UHS	2.8308475528290844e-17	103.14386448347236	135.69894214645325	139.0%
GWW	TWTR	6.1040150357

MU	ULTA	-1.4154237764145422e-17	43.49149536801525	299.32310850591773	111.9%
NWS	TEL	7.430974826176346e-17	12.990613736004468	85.88839013453024	111.9%
ADM	STX	-3.538559441036356e-17	38.61159351242491	45.93226144798248	111.9%
DLTR	MTB	-5.307839161554533e-18	103.14386448347236	150.58535736205567	111.9%
FRC	TXN	-1.0615678323109067e-16	100.31733341900951	110.8989408272671	111.9%
DLR	ORCL	-6.015551049761804e-17	110.37169717127584	51.97681785674684	111.9%
HSIC	WDC	1.4154237764145422e-16	64.67094448743113	50.43285378991845	111.9%
EA	HUM	2.8308475528290844e-17	96.28862115016496	283.9367532312158	111.9%
DRE	EW	1.026182237900543e-16	30.366976726577576	67.94626827164001	111.9%
IQV	ORLY	2.1231356646218133e-17	145.84039884164514	394.8825897581549	111.9%
CMI	FMC	1.3092669931834516e-16	153.0268819132649	80.45333836468093	111.9%
NSC	TDG	1.1323390211316335e-16	179.24853570337788	458.2647673466291	111.9%
CSCO	EXC	-2.1231356646218133e-17	47.60303603700433	30.669482409716604	111.9%
GWW	INTU	-7.032886889059

GLW	MAR	-4.2462713292436265e-17	28.89878171943573	129.95632606293574	108.9%
BBY	AVGO	-8.492542658487253e-17	66.77334164623245	268.348134196612	108.9%
SNA	VMC	-4.9539832174508976e-17	150.03159359631786	129.29391579798968	108.9%
A	HOLX	-8.492542658487253e-17	74.74333203076367	48.18812769247716	108.9%
KLAC	TER	4.865519231424989e-17	131.7944294294988	51.33483355548752	108.9%
ODFL	POOL	8.846398602590887e-17	107.26304377217691	184.18961088020964	108.9%
NVR	DIS	6.36940699386544e-17	3338.889723333229	131.44761204814532	108.9%
APD	PLD	3.9808793711659e-18	200.4855531487332	75.95357145636206	108.9%
DPZ	FB	-2.8308475528290844e-17	260.5725640528706	185.3225893423377	108.9%
ADI	DUK	-1.2296494057601334e-16	106.2334629377996	80.72304082011796	108.9%
EA	CAH	-6.104015035787713e-17	96.28862115016496	44.11207080552303	108.9%
MCK	PKG	-5.307839161554533e-18	130.9063196676186	94.39975455842644	108.9%
AMCR	COF	-4.9539832174508976e-17	9.437798283489576	87.06105764928567	108.9%
ALGN	COST	0.0	253.7599598554026	2

CF	HPE	-7.077118882072711e-18	42.06480065759909	13.93751433551074	107.0%
MU	NOC	-4.9097512244379426e-17	43.49149536801525	312.6019739401768	107.0%
EMR	IPG	7.430974826176346e-17	63.14752080241048	19.8526777594213	107.0%
IRM	SWK	-7.077118882072711e-17	27.370877155744697	137.88997431295326	107.0%
KMX	WMT	7.784830770279983e-17	81.45940244150351	105.10226501221676	107.0%
CBRE	ULTA	4.2462713292436265e-17	52.16003983334241	299.32310850591773	107.0%
BBY	PKG	1.0615678323109066e-17	66.77334164623245	94.39975455842644	107.0%
COO	LMT	7.077118882072711e-17	304.8813375647799	331.9957525853617	107.0%
SHW	TXN	7.077118882072711e-18	162.3488270125066	110.8989408272671	107.0%
LYB	WAT	-6.36940699386544e-17	76.44202679941854	222.66729073695453	107.0%
ANET	GS	2.8308475528290844e-17	61.71735049243942	196.94752624025384	107.0%
DISCA	WY	6.015551049761804e-17	29.29095614003945	23.966735649868788	107.0%
SPGI	SO	3.538559441036356e-17	231.30257984176572	50.62477522162328	107.0%
CL	ITW	6.36940699386544e-17	65.47627

EQIX	TER	-8.492542658487253e-17	489.5879448514536	51.33483355548752	105.4%
DLTR	SYF	1.0615678323109066e-17	103.14386448347236	31.719131918067475	105.4%
INCY	PSA	1.7692797205181777e-17	82.25713153854309	210.64650632090775	105.4%
NWS	SNA	1.0615678323109067e-16	12.990613736004468	150.03159359631786	105.4%
NVR	V	5.1309111895027146e-17	3338.889723333229	166.93790742790557	105.4%
GILD	K	1.4154237764145422e-17	60.42897398443336	55.10002573932785	105.4%
CAT	WHR	0.0	125.1710677431874	131.8149366644749	105.4%
ABBV	AKAM	9.907966434901795e-17	67.68055960666611	81.495537989643	105.4%
ADSK	COST	-1.273881398773088e-16	161.68474138115508	255.1612077082296	105.4%
COST	VRTX	1.7692797205181777e-17	255.1612077082296	187.00868486503205	105.4%
BMY	CVS	-5.307839161554533e-18	47.022757100868986	57.29052596073227	105.4%
BIIB	WBA	-7.254046854124529e-17	261.66737025287523	53.10900182837984	105.4%
AVGO	PNR	1.424270175017133e-16	268.348134196612	38.44404632446776	105.4%
EXC	SBNY	-3.6270234270622636e-17	30.66948240

...

ADBE	DAL	1.074837430214793e-16	284.53868607600845	54.9055970484517	73.0%
MA	RCL	6.36940699386544e-17	258.58022068221254	114.37079431906164	73.0%
ALGN	EIX	4.2462713292436265e-17	253.7599598554026	60.18401333630322	73.0%
NWL	NCLH	-3.538559441036356e-17	15.236730161416103	53.30956168003766	73.0%
AAPL	BEN	-4.2462713292436265e-17	53.07020118986943	27.367396806815705	73.0%
AMP	MRO	0.0	135.77993567721302	13.597195610107178	73.0%
IDXX	WAB	-3.8924153851399907e-17	253.5109957508832	71.26423775722306	73.0%
ADBE	FCX	0.0	284.53868607600845	11.083436346624	73.0%
CMG	CTRA	1.1323390211316335e-16	741.5357763282806	21.36968126714942	73.0%
CMG	TRV	9.200254546694524e-17	741.5357763282806	131.96073162793164	73.0%
KEYS	WRK	-1.2031102099523608e-16	91.34908394984517	34.99886358496677	73.0%
ANSS	BA	-2.8308475528290844e-17	207.610517707004	358.7206766196931	73.0%
BK	LRCX	2.8308475528290844e-17	44.26618383035242	209.00412564828576	73.0%
AAPL	DISH	6.36940699386544e-17	53.07020118986943	34.573904364232526	73.0%
PG

EPAM	MET	1.1323390211316335e-16	181.92501989113856	42.68809326901379	70.9%
TECH	PBCT	6.723262937969076e-17	199.6340913202658	14.38808724224805	70.9%
NKE	OXY	-2.8308475528290844e-17	86.10080907449304	47.59877840931197	70.9%
HBAN	ZBRA	1.114646223926452e-16	12.318580718629388	211.1878483988849	70.9%
DD	ETN	5.661695105658169e-17	67.90307840598057	60.95059152428372	70.9%
MMM	LRCX	-4.2462713292436265e-17	163.14480615137109	209.00412564828576	70.9%
KLAC	RF	2.8308475528290844e-17	131.7944294294988	14.091663390991696	70.9%
BRO	KHC	2.8308475528290844e-17	33.39336529765946	28.32533654748681	70.9%
DG	VNO	-7.077118882072711e-17	136.15358551754895	55.55739464322884	70.9%
IP	KLAC	0.0	36.9586316446859	131.7944294294988	70.9%
EPAM	GPC	8.492542658487253e-17	181.92501989113856	94.26432478095433	70.9%
CTLT	XOM	4.2462713292436265e-17	48.75996006817456	62.22162862222983	70.9%
EMN	MPWR	4.9539832174508976e-17	69.97532602135404	144.33122742793475	70.9%
CTLT	PSX	2.6981515737902208e-17	48.75996006817456	89.41928

LH	PAYC	-4.9539832174508976e-17	163.35709128816765	217.99932302041836	67.7%
PVH	TGT	8.492542658487253e-17	99.43343523489052	89.99990759617779	67.7%
CHRW	NOW	-4.6001272733472624e-17	79.7344851246868	260.5661749972765	67.7%
JNPR	KEYS	2.8308475528290844e-17	23.70833956197913	91.34908394984517	67.7%
PH	WFC	-2.5654555947513576e-17	170.76980116642804	45.539227443862245	67.7%
AMD	STX	-3.8924153851399907e-17	31.366175320993857	45.93226144798248	67.7%
AIZ	PAYC	5.838623077709985e-17	107.75131973327392	217.99932302041836	67.7%
BR	MTCH	-6.36940699386544e-17	114.7043882879128	69.56227107257007	67.7%
CDNS	IRM	-3.538559441036356e-17	65.84828672371063	27.370877155744697	67.7%
AMCR	NOW	-1.1323390211316335e-16	9.437798283489576	260.5661749972765	67.7%
CB	NOW	2.653919580777267e-17	139.98837912510115	260.5661749972765	67.7%
FCX	JNPR	4.5116632873213536e-17	11.083436346624	23.70833956197913	67.7%
FCX	MA	7.077118882072711e-18	11.083436346624	258.58022068221254	67.7%
MSCI	LUV	3.18470349693272e-17	219.84879597

MTCH	GSPC	2.1231356646218133e-17	69.56227107257007	2947.94648748755	62.7%
ADBE	ETSY	2.8308475528290844e-17	284.53868607600845	57.5963944818869	62.7%
AMD	J	-2.1231356646218133e-17	31.366175320993857	81.3010425643617	62.7%
ETN	MHK	1.1323390211316335e-16	60.95059152428372	133.72250971091222	62.7%
CTLT	MHK	1.273881398773088e-16	48.75996006817456	133.72250971091222	62.7%
QCOM	WBA	-2.8308475528290844e-17	69.22771739579767	53.10900182837984	62.7%
GNRC	WTW	-1.4154237764145422e-17	72.32557777009637	180.02670458303504	62.7%
TAP	PYPL	9.907966434901795e-17	54.06843580572728	106.27513949329636	62.7%
TER	TXT	5.661695105658169e-17	51.33483355548752	49.00436073090451	62.7%
MTCH	NVR	1.0615678323109066e-17	69.56227107257007	3338.889723333229	62.7%
FCX	NI	8.846398602590887e-17	11.083436346624	25.711676145454803	62.7%
GNRC	MMC	-8.492542658487253e-17	72.32557777009637	94.71629123763734	62.6%
RMD	SLB	-1.4154237764145422e-17	122.00426759757843	35.739551012259554	62.6%
NOW	LUV	9.465646504772251e-17	260.566174

STZ	SEDG	2.8308475528290844e-17	182.49336212279783	66.2237252923122	43.6%
AMD	DISH	5.661695105658169e-17	31.366175320993857	34.573904364232526	43.6%
CSX	PENN	1.0615678323109067e-16	23.52349455328101	21.33617534865421	43.6%
SEDG	URI	2.8308475528290844e-17	66.2237252923122	131.56992054365546	43.5%
SEDG	WMB	5.661695105658169e-17	66.2237252923122	21.4232702445224	43.4%
PNR	SEDG	-8.492542658487253e-17	38.44404632446776	66.2237252923122	43.4%
AJG	ETSY	0.0	83.37104879432465	57.5963944818869	43.4%
AMD	BEN	-4.2462713292436265e-17	31.366175320993857	27.367396806815705	43.3%
AMD	NLSN	-5.661695105658169e-17	31.366175320993857	21.822404709470224	43.2%
GS	SEDG	-4.2462713292436265e-17	196.94752624025384	66.2237252923122	43.2%
SEE	SEDG	-8.492542658487253e-17	40.38892995218832	66.2237252923122	43.1%
SEDG	PARA	5.661695105658169e-17	66.2237252923122	42.58536275734465	43.0%
ABMD	SEDG	2.8308475528290844e-17	241.5657365654569	66.2237252923122	42.8%
AMD	WBA	-7.077118882072711e-17	31.366175320993857	53.109001